In [1]:
import numpy as np
import os
import librosa
import IPython.display as ipd 
import plotly.graph_objects as go

In [2]:
# Set directory path var
# BASE_DIR= f'{os.getcwd()}/sound_folder/'
BASE_DIR= f'{os.getcwd()}\\sound_folder\\'  #Window
audio_file = "debussy_arabesque_no1.wav"
audio_path = os.path.join(BASE_DIR, audio_file)

# Check if the path is working
print(audio_path) 

c:\Users\gina0\Desktop\fourier_analysis\capstone\sound_folder\debussy_arabesque_no1.wav


In [3]:
# Play sound clip
'''
sr(sample rate): int 
    number of audio points sampled per second = 22050 22.05Hz
audio_data: ndarray(N)
    discrete audio data as an array of length N(audio length*sr)
'''
audio_data, sr = librosa.load(audio_path)
audio_data = audio_data[:sr*20]
audio_data.shape
ipd.Audio(audio_data, rate = sr)

In [11]:
# Define FFT function
# Referred to https://www.youtube.com/watch?v=65EYg6enKFs
def compute_fft(x):
    '''
    parameters
    ----------
    x : ndarray
        discrete data of time domain
    sr : int
        sample rate 
    return
    ------    
    '''
    N = len(x) #num of points
    freq_num = int(np.ceil(N/2)) #
    x_fft = np.fft.fft(x)

    #devide by N to normalize the amplitude of the sum, 
    #multiply by 2 as we only consider the positive half of the spectrum for real signals 
    real_part = (2/N)*np.real(x_fft)[0:freq_num] 
    imag_part = (2/N)*np.imag(x_fft)[0:freq_num]
    return x_fft, real_part, imag_part

In [12]:
x_fft, x_fft_real, x_fft_imag = compute_fft(audio_data)

In [13]:
# Plot FFT graph
# 1. Set variables.
audio_data, sr = librosa.load(audio_path)
audio_data = audio_data[:sr*20]
N = len(audio_data) 
T = N//sr

# 2. Set x-, y-axis arrays in the frequency domain
amps = np.sqrt(x_fft_real**2 + x_fft_imag**2) 
freqs = np.linspace(0, len(x_fft_real)/T, len(x_fft_real))

# 3. Create band pass filter
one_sided_x_fft = x_fft[:len(amps)]

low_cutoff = 4100*T
low_pass_mask = np.zeros(len(amps), dtype=int)
low_pass_mask[:low_cutoff] = 1
high_cutoff = 100*T
high_pass_mask = np.zeros(len(amps), dtype=int)
high_pass_mask[high_cutoff:] = 1
band_pass_mask = high_pass_mask & low_pass_mask

# 4. Create threshhold filter
threshold = 0.0000025
threshold_mask = np.where(amps >= threshold, 1, 0)

# 5. Apply filters
final_mask = band_pass_mask & threshold_mask
filterd_fft = one_sided_x_fft * final_mask
filterd_amps = amps * final_mask

# 3. Generate graphs
# Original FFT
fig = go.Figure()
fig.add_traces(go.Scatter(
    x=freqs[::T],
    y=amps[::T],
    mode='lines+markers',
    marker_size=5,
    name='FFT Result',)
)


# Filter applied FFT
fig.add_traces(go.Scatter(
    x=freqs[::T],
    y=np.abs(np.real(filterd_amps[::T])),
    mode='lines+markers',
    marker_size=5,
    line=dict(color='rgba(255, 182, 193, 0.4)'),
    name='Filtered FFT',
    visible='legendonly'
    )
)
fig.update_layout(
    title=dict(
        text='FFT Result',
        xanchor='center',
        x=0.5,
        font_size=30
    ),
    font = dict(
        family='Raleway'
    ),
    xaxis_title=dict(
        text='Frequencies(Hz)',
        font_size=20
    ),
    yaxis_title=dict(
        text='Amplitude',
        font_size=20
    ),
    legend=dict(
        font_size=15,
    )
)
fig.show()


fig = go.Figure()
# Band pass filter
fig.add_traces(go.Scatter(
    x=freqs[::T],
    y=band_pass_mask[::T],
    mode='lines',
    line=dict(color='rgba(221, 160, 221, 1.0)'),
    name='Band Pass Filter',
    visible='legendonly'
))

# Threshold filter
fig.add_traces(go.Scatter(
    x=freqs[::T],
    y=threshold_mask[::T],
    mode='lines',
    line=dict(color='rgba(173, 216, 230, 0.6)'),
    name='Threshold Filter',
    visible='legendonly'
))
# 
fig.update_layout(
    title=dict(
        text='Filters ',
        xanchor='center',
        x=0.5,
        font_size=30
    ),
    font = dict(
        family='Raleway'
    ),
    xaxis_title=dict(
        text='Frequencies(Hz)',
        font_size=20
    ),
    yaxis_title=dict(
        text='Amplitude',
        font_size=20
    ),
    legend=dict(
        font_size=15,
    )
)


In [14]:
# Define inverse IFFT
def compute_ifft(one_sided_x_fft):
    '''
    parameters
    ----------
    amps : ndarray
    return
    ------
    real_part_x
    imag_part_x
    '''

    n_half= len(one_sided_x_fft)
    N = n_half * 2
    x_fft = np.zeros(N, dtype=complex)
    x_fft[:n_half] = one_sided_x_fft
    x_fft[n_half+1:] = np.conj(x_fft[:n_half:-1])

    real_part_x = np.real(np.fft.ifft(x_fft))
    imag_part_x = np.imag(np.fft.ifft(x_fft))
    return real_part_x, imag_part_x

In [15]:
filtered_real_x, filtered_imag_x = compute_ifft(filterd_fft)

In [16]:
from IPython.display import display, HTML

audio_orig = ipd.Audio(audio_data, rate=sr)
audio_filtered = ipd.Audio(filtered_real_x, rate=sr)
html = f"""
<table>
  <tr>
    <th>Original</th>
    <th>Filtered</th>
  </tr>
  <tr>
    <td>{audio_orig._repr_html_()}</td>
    <td>{audio_filtered._repr_html_()}</td>
  </tr>
</table>
"""
display(HTML(html))

In [17]:
time = np.linspace(0,T,len(audio_data))
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=time[::T*2],
    y=audio_data[::T*2],
    mode='lines',
    line=dict(color='rgba(173, 216, 230, 0.6)'),
    name='Original')
)

fig.add_trace(go.Scatter(
    x=time[::T*2],
    y=filtered_real_x[::T*2],
    mode='lines',
    name='Filtered',
    line=dict(color='rgba(255, 182, 193, 0.8)')
    )
)
fig.update_layout(
    font = dict(
        family='Raleway'
    ),
    title=dict(
        text='Audio Wave',
        x=0.5,
        xanchor='center',
        yanchor='top',
        font_size=24
    ),
    xaxis_title=dict(
        text='Time(s)',
        font_size=20
    ),
    yaxis_title=dict(
        text='Amplitude',
        font_size=20
    ),
    legend=dict(
        font_size=15,
    )
)